# Monte Carlo Simulation of cooling energy demand in Swiss office building stock with different climate scenarios

## Introduction

Cooling energy demand is projected to increase significantly in the near future, driven especially by climate change and the increasing frequency of heat waves.

In this exercise, we will model the cooling energy demand in Swiss office buildings using Monte Carlo (MC) methods. We well use the model to explore the impacts of climate change on energy demand using different climate scenarios.

### Part 1

In Part 1 we will define the cooling energy demand model and get distributions for its inputs from real data.

### Part 2

In Part 2 we will investigate the impact of climate change on cooling demand, as well as the effect of improving the COP.


# Set up the Python workspace

In [ ]:
# Load the Python packages we need
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy import stats

# Some packages have strange names, we can also rename them
from tqdm import tqdm as progress_bar

# Plotting Configuration
plt.rcParams['figure.dpi'] = 100
plt.rcParams['savefig.dpi'] = 300
plt.rcParams['savefig.bbox'] = 'tight'

# Load the data for the exercise

## Define the number of office buildings in Switzerland


In [ ]:
NUMBER_OFFICES_IN_SWITZERLAND_TODAY = 13484

## Load the data about the buildings with cooling systems

This is information drawn from a study on the certificates given for cooling systems in Geneva [1]. It includes:

- The building non-residential area
- The thermal power per unit area $P_{th, m2}$
- The cooling systme coefficient of performance (COP)
- The number of hours per year that the cooling system operates ($NH$)


[1] Hollmuller, Pierre, Stefan Michael Hunziker, and Bernard Marie Lachal. 2011. “Enjeux de La Climatisation Au Niveau Genevois et Tour d’horizon de Possibles Alternatives.” http://archive-ouverte.unige.ch/unige:23581.

In [ ]:
COOLING_DATA_GENEVA = pd.read_csv('cooling_data_geneva.csv')

The data is loaded as a *Data Frame*, which is similar to an Excel table with rows and columns. We can check the first few rows in the table using the `head()` function.

In [ ]:
COOLING_DATA_GENEVA.head()

Use the `describe()` function to summarise information about the input data.

In [ ]:
COOLING_DATA_GENEVA.describe()

We can access the values of a single column using its name, e.g.for the `non_residential_area` column:

In [ ]:
COOLING_DATA_GENEVA['non_residential_area'].head()

# Exercise Part 1: Estimate the cooling demand and uncertainty in office buildings for today

# 1. Define a deterministic model


## Cooling demand model for a single office building

$E_{i, el cool} [kWh] = \Psi * A * NH  *  P_{TH,m2}/COP$

- $E_{i, el, cool} $ : the total energy for cooling per year for a building $i$
- $\Psi$ : A number which determines if the building has cooling or not, equal to either 1 (has cooling) or 0 (no cooling)
- $NH$ : the number of hours the cooling system operates every year
- $A$ : the non-residential floor area of the building
- $P_{TH,m2}$ : The thermal power need for cooling of the building
- $COP$ :  the Coefficient of Performance of the cooling system


## Cooling demand for all office buildings

The total cooling demand for all N office buildings in Switzlerland is the sum over all buildings:

$$
E_{el cool} [kWh] = \sum^N_i E_{i, el cool}
$$


# 2. Define probability distribution parameters for the inputs

In this section we will develop probability distributions for the parameters defined in section 1.

We will be using a tool in Python (Scipy) that allows us to create probability distribution variables that save the distribution parameters so we can use them again later.

##  Probability of a building having cooling

Whether or not a building has cooling is a *binary decision*: it is either `True` or `False` (*yes* or *no*). In this case, we use the **Bernoulli** distribution that takes the value 1 with probability $p$ and the value 0 with probability $q = 1 − p$. 

We will use a result that was previously calculated where the probability is 0.225.

In [ ]:
PROBABILITY_OF_COOLING_TODAY = 0.225

In [ ]:
IS_COOLED_DISTRIBUTION = stats.bernoulli(PROBABILITY_OF_COOLING_TODAY)

## COP distribution

We can find the mean and standard deviation of the COP to prepare a normal distribution. We use the function `np.mean` to calculate the mean of an array of values and the function `np.std` to calculate the standard deviation $\sigma$


In [ ]:
COP_MEAN = np.mean(COOLING_DATA_GENEVA['cop'])
COP_SIGMA = np.std(COOLING_DATA_GENEVA['cop'])

print('Mean COP ', COP_MEAN)
print('Standard Deviation of COP ', COP_SIGMA)

In [ ]:
COP_DISTRIBUTION = stats.norm(COP_MEAN, COP_SIGMA)

In [ ]:
# Create a figure
figure, axes = plt.subplots()

# Plot the data
axes.hist(COOLING_DATA_GENEVA['cop'], density=True, label='COP distribution')

# Plot the Probability Density Function
x = np.linspace(0, 7, 100)
axes.plot(x, COP_DISTRIBUTION.pdf(x), label='Normal distribution')

axes.set(
    xlabel='COP',
)

axes.legend()

figure.savefig('COP normal distribution plot.png')
figure.show()

## Distribution of the cooling thermal power demand per unit area $P_{TH,m2}$

Each building has a certain need of cooling power i.e. the rate of thermal energy to be removed from the building. Combined with the COP of the cooling system this will tell us the electrical power needed by the system (see equations in introduction).

### Plot the $P_{TH,m2}$ data compared with a normal distribution

First we compare the distribution of data with a normal distribution. We calculate the mean and standard deviation, which we use to generate a normal distribution for the comparison.

**NOTE:** Here we will also introduce code to plot graphs. You can use this code again later.

> **EXERCISE: Do the skewness and kurtosis test statistics indicate that the distribution of $P_{TH,m2}$ is normal? What other information about the Thermal Power demand is important in understanding the suitability of the normal distribution? Hint: can normally distributed values be less than zero?**


In [ ]:
stats.normaltest(COOLING_DATA_GENEVA['pth_m2'])

In [ ]:
stats.skewtest(COOLING_DATA_GENEVA['pth_m2'])

In [ ]:
stats.kurtosistest(COOLING_DATA_GENEVA['pth_m2'])

In [ ]:
mean = np.mean(COOLING_DATA_GENEVA['pth_m2'])
standard_deviation = np.std(COOLING_DATA_GENEVA['pth_m2'])

# Create a figure with one set of axes (i.e. one subplot)
figure, axes = plt.subplots()

# Plot the data on the axes
axes.hist(COOLING_DATA_GENEVA['pth_m2'], density=True, label='Thermal power distribution')

# Plot the Probability Density Function on the axes
x = np.linspace(-0.5, 0.5, 100)
axes.plot(x, stats.norm.pdf(x, mean, standard_deviation), label='Normal distribution')

axes.set(
    xlabel='Thermal Power Demand (kW/m2)',
)

axes.legend()

figure.savefig('thermal power normal distribution plot.png')
figure.show()

### Plot the data compared with a log-normal distribution

The log-normal distribution is closely related to the normal distribution, but it's value cannot negative, making it *skew* compared to the normal distribution. It is a good place to start for distributions of values that are random but always greater than zero.

We can fit distributions to empirical data by calculating the Maxiumum Liklihood Estimate (MLE) for the distribtuion parameters using the `fit` function. However there is no guarantee that the fitted distribution is actually a good match for the observed distribution - the `fit` function only tells you the values of the parameters that give the *closest* approximation (which might still be quite far off). Therefore we also plot the data to check.


In [ ]:
shape, loc, scale = stats.lognorm.fit(COOLING_DATA_GENEVA['pth_m2'])

PTH_DISTRIBUTION = stats.lognorm(shape, loc, scale)

In [ ]:
# Create a figure
figure, axes = plt.subplots()

# Plot the data
axes.hist(COOLING_DATA_GENEVA['pth_m2'], density=True, label='Thermal power distribution')

# Plot the Probability Density Function
x = np.linspace(0, 0.5, 100)
axes.plot(x, PTH_DISTRIBUTION.pdf(x), label='Log-Normal distribution')

axes.set(
    xlabel='Thermal Power Demand [kW/m2]',
)

axes.legend()

figure.savefig('thermal power lognormal distribution plot.png')
figure.show()

# Estimate distribution of cooling hours $NH$

We need to model the number of operating hours ($NH$) of the heating system.

We know that a log-normal distribution should be better than a normal distribution, because NH must be above zero. 

## First (unsuccessful) approach

As mentioned before, just because we can `fit` a distribution to the data, it doesn't mean the fit is a good one!

Let's plot the data and the lognormal distribution.


In [ ]:
s, loc, scale = stats.lognorm.fit(COOLING_DATA_GENEVA['nh'])

BAD_NH_DISTRIBUTION = stats.lognorm(s, loc, scale)

In [ ]:
# Create a figure
figure, axes = plt.subplots()

# Plot the data
axes.hist(COOLING_DATA_GENEVA['nh'], density=True, label='NH distribution')

# Plot the distribution
x = np.linspace(100, 8000, 100)
axes.plot(x, BAD_NH_DISTRIBUTION.pdf(x), label='Log-Normal distribution')

figure.show()

## Second (better) approach.

The observed data is very spread out over a large range, which means that a fitting a log-normal distribution doesn't work!

A common approach in statistics when data is spread over a very large range is to take the natural logarithm ($log_e$ or $ln$) of the values. This scales the values to a smaller range, which then allows familiar statistical tools to work. Therefore, we approximate the NH distribution by fitting a lognormal distribtuion to the **log** of the NH data $log(NH)$.

We use the function `np.log` to calculate the $log$ of an column of numbers in the data table.

**Important:** When we generate a value from the distribution, we then need to **exponent** ($e^x$ which is the inverse of taking the log) of that value to get the actual value of NH:

$$
NH = e^{x}
$$

Where $x$ is a value drawn from the log-normal distribution.

In [ ]:
log_nh = np.log(COOLING_DATA_GENEVA['nh'])

s, loc, scale = stats.lognorm.fit(log_nh)
NH_DISTRIBUTION = stats.lognorm(s, loc, scale)

In [ ]:
# Create a figure
figure, axes = plt.subplots()

# Plot the data
axes.hist(np.log(COOLING_DATA_GENEVA['nh']), density=True, label='NH distribution')

# Plot the Probability Density Function
x = np.log(np.linspace(100, 8000, 100))
axes.plot(x, NH_DISTRIBUTION.pdf(x), label='Log-Normal distribution')

axes.legend()

figure.show()

# Distribution of floor area $A$

Estimate the distributions of floor areas of the office buildings. Like for $NH$, these values are spread over a very wide range so we must first calculate the `log`. We fit a distribution to the values of $log(A)$. As for $NH$, when we want to pick a random value for A, when we pick a value $v$ from the distribution, we need to calculate the area as $A = e^{v}$


In [ ]:
log_A = np.log(COOLING_DATA_GENEVA['non_residential_area'])

s, loc, scale = stats.lognorm.fit(log_A)

A_DISTRIBUTION = stats.lognorm(s, loc, scale)

In [ ]:
# Create a figure
figure, axes = plt.subplots()

# Plot the data
axes.hist(np.log(COOLING_DATA_GENEVA['non_residential_area']), density=True, label='A distribution')

# Plot the Probability Density Function
x = np.log(np.linspace(100, 17000, 100))
axes.plot(x, A_DISTRIBUTION.pdf(x), label='Log-Normal distribution')

axes.legend()

figure.show()

# 3. Apply the distributions to the deterministic model model

## Running the model manually to calculate the total demand for all the office buildings in Switzerland

To model all Swiss office buildings, we need to pick as many values from the probability distributions as there are office buildings in Switzerland. At the beginning of the notebook, we defined the variable `NUMBER_OFFICES_IN_SWITZERLAND_TODAY = 13484`. 

We can generate this number of values from our distributions and calculate the sum of the energy demands for all the buildings. 

We pick random values from the distribution variables we defined ( `COP_DISTRIBUTION` etc...) using the `rvs()` function (short for Random ValueS). We can pick many values at once and the `rvs()` function will generate an *array* of numbers (like a column in Excel). We can add, multiply, and divide these arrays similarly to how we work with single numbers (scalars).

e.g. Running `COP_DISTRIBUTION.rvs(10)` will pick 10 values from the COP distribution. 

Remember that for the distributions of number of operation hours $NH$ and floor area $A$ we need to pick a value and then calculate its exponent using the `np.exp()` function.

We then use the `np.sum()` function to get the sum of all results for energy. The output units are **GWh/year**.


> **EXERCISE: Run the calculation of the total energy demand manually 5 times. Record each value in a table. Calculate the mean and standard deviation of the values. With reference to the central limit theorem, explain why we analyse the sums of total energy demand.**

In [ ]:
##############################################################
# Draw from the distribution of whether the building is cooled
psi = IS_COOLED_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)

##################################################
# DRAW FROM THE COP DISTRIBUTION
COP = COP_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)

##################################################
# DRAW FROM THE THERMAL POWER DEMAND DISTRIBUTION
P_TH = PTH_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)

################################
# DRAW FROM THE NH DISTRIBUTION
# IMPORTANT: don't forget to calculate the EXPONENT of the random values for NH
NH = np.exp(NH_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY))

################################
# DRAW FROM THE AREA DISTRIBUTION
# IMPORTANT: don't forget to calculate the EXPONENT of the random values for A
A = np.exp(A_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY))

################################
# Apply the cooling model
E_el_cool = psi * A * NH * P_TH / COP

##########################################
# Calculate the sum of the cooling demand
# Convert the result from kWh to GWh 
E_el_cool_total = np.sum(E_el_cool) / 1_000_000

print('Total cooling electricity demand =', E_el_cool_total , 'GWh')

## Running the model in a loop

Running a model manually is very slow and boring! Instead, we use a **loop** and collect the results for each iteration. 

This is the essence of Monte Carlo simulation: Since we are picking from the distribution every time, each run will give a slightly different answer. 
By running the distribution enough times, we get a distribution of the possible outputs. From this, we get both *mean* values and *standard error* in these values. The Standard Error tells us about the uncertainty in the output as a function of the distributions of the inputs.


In [ ]:
# IMPORTANT: please do not increase this number to over 10,000 to avoid the program taking a very long time
N_ITERATIONS = 10

# Create an empty list that will contain the results.
RESULTS_PRESENT_DAY = list()

# Run the model N times
# Add a progress bar so we can see what is happening
for run_number in progress_bar(range(N_ITERATIONS)):
    
    ##############################################################
    # Draw from the distribution of whether the building is cooled
    psi = IS_COOLED_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)
    
    ##################################################
    # DRAW FROM THE COP DISTRIBUTION
    COP = COP_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)

    ##################################################
    # DRAW FROM THE THERMAL POWER DEMAND DISTRIBUTION
    P_TH = PTH_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)

    ################################
    # DRAW FROM THE NH DISTRIBUTION
    # IMPORTANT: don't forget to calculate the EXPONENT of the random values for NH
    NH = np.exp(NH_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY))

    ################################
    # DRAW FROM THE AREA DISTRIBUTION
    # IMPORTANT: don't forget to calculate the EXPONENT of the random values for A
    A = np.exp(A_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY))

    ################################
    # Apply the cooling model
    E_el_cool = psi * A * NH * P_TH / COP
    
    ##########################################
    # Calculate the sum of the cooling demand
    # Convert the result from kWh to GWh 
    E_cooling_total = np.sum(E_el_cool) / 1000000
    
    # Add the results to the list of results
    RESULTS_PRESENT_DAY.append(E_cooling_total)
    

# 4. Analyse the results

The variable `RESULTS_PRESENT_DAY` contains a list of the results of the model run. To get the value and its uncertainty, we must now calculate the mean of the values and the standard error (95% confidence interval). When we report uncertainty values as X±Y, the value of Y is usually the 95% confidence interval. This can be calculated as 1.96 x standard deviation.

NOTE: all totals have been converted from kWh/year to GWh/year.

> **EXERCISE: Run the MC simulation for 10, 100, 1000 iterations by changing the value of `N_ITERATIONS` above.**

In [ ]:
# Create a figure
figure, axes = plt.subplots()

axes.hist(RESULTS_PRESENT_DAY, density=True, bins=20 ,label='Demand distribution')
axes.set(
    xlabel='Cooling electricity demand [GWh]'
)

figure.savefig('cooling electricity demand.png')
figure.show()

In [ ]:
print('Mean: ', np.mean(RESULTS_PRESENT_DAY))

In [ ]:
print('Standard Deviation: ', np.std(RESULTS_PRESENT_DAY))

# Part 2: Exploring Climate Scenarios for 2050

The increase in temperature from climate change has two effects on cooling demand:

1. Increasing temperatures means that cooling systems work more often. This can be measured by the change in Cooling Degree Days (CDD).
2. Increasing temperatures means that more people install cooling. This can be measured by change in the probability of buildings being cooled - these have been calculated for you by Xiang Li.


Below is a table presenting these values for the present day and for two Representative Climate Pathways (RCP).

- RCP 2.6 is a low emissions scenario
- RCP 8.5 is a high emissions scenario

|                             | Present | RCP 2.6 | RCP 8.5 |
|-----------------------------|---------|---------|---------|
| CDD                         | 213.7   | 276.7   | 365.2   |
| Probability of being cooled | 0.225   | 0.5455  | 0.5677  |



We can investigate the effect of the change in CDD and change in probability of cooling on the total cooling demand. We can model the impact of changing CDD by assuming that the number of operation hours $NH$ is proportional to the CDD. Therefore we calculate the new value of $NH$ by scaling using the ratio of the scenario CDD to the present day CDD:

$$
NH_{scenario} = \frac{CDD_{scenario}}{CDD_{\text{present day}}} * NH_{\text{present day}}
$$


> **EXERCISE: Tablute and create a graph of the results for the different scenarios. Calculate the change in cooling energy demand in total and as a percentage. Calculate the *uncertainty* in the change in both the total and the percentage**


## Run the function with the inputs from the table

- The function gives you a pair of values: the total cooling demand (mean of the model iterations) and the confidence interval.

### The results for today is shown here as an example

In [ ]:
###############################################
# CHANGE THIS VARIABLE TO SET THE SCENARIO CDD
SCENARIO_CDD = 276.7

##################################################
# CHANGE THIS VARIABLE THE PROBABILITY OF COOLING
COOLING_PROBABILITY = 0.5455



##################################################
# Creates a new probability distribution
# with the new probability
NEW_IS_COOLED_DISTRIBUTION = stats.bernoulli(COOLING_PROBABILITY)

##################################################
# Number of iterations
# DO NOT CHANGE
fixed_N_iterations = 1000

# Create a list to hold the results
results = list()

# Run the model N times
# Add a progress bar so we can see what is happening
for run_number in progress_bar(range(fixed_N_iterations)):

    ##############################################################
    # Draw from the distribution of whether the building is cooled
    psi = NEW_IS_COOLED_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)
    
    ##################################################
    # DRAW FROM THE COP DISTRIBUTION
    # HINT: This is where you can adjust the COP values
    COP = COP_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)

    ##################################################
    # DRAW FROM THE THERMAL POWER DEMAND DISTRIBUTION
    P_TH = PTH_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)

    ################################
    # DRAW FROM THE NH DISTRIBUTION
    # IMPORTANT: don't forget to calculate the EXPONENT of the random values for NH
    NH = np.exp(NH_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY))
     
    ##################################################
    # APPLY THE SCALING OF NH WITH THE CDD
    ##################################################
    NH = NH * SCENARIO_CDD / 213.7

    ################################
    # DRAW FROM THE AREA DISTRIBUTION
    # IMPORTANT: don't forget to calculate the EXPONENT of the random values for A
    A = np.exp(A_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY))

    ################################
    # Apply the cooling model
    E_el_cool = psi * A * NH * P_TH / COP

    ##########################################
    # Calculate the sum of the cooling demand
    # Convert the result from kWh to GWh     
    E_cooling_total = np.sum(E_el_cool) / 1000000

    results.append(E_cooling_total)
    
print('Mean: ', np.mean(results))
print('Standard Deviation: ', np.std(results))

In [ ]:
###############################################
# CHANGE THIS VARIABLE TO SET THE SCENARIO CDD
SCENARIO_CDD = 365.2

##################################################
# CHANGE THIS VARIABLE THE PROBABILITY OF COOLING
COOLING_PROBABILITY = 0.5677



##################################################
# Creates a new probability distribution
# with the new probability
NEW_IS_COOLED_DISTRIBUTION = stats.bernoulli(COOLING_PROBABILITY)

##################################################
# Number of iterations
# DO NOT CHANGE
fixed_N_iterations = 1000

# Create a list to hold the results
results = list()

# Run the model N times
# Add a progress bar so we can see what is happening
for run_number in progress_bar(range(fixed_N_iterations)):

    ##############################################################
    # Draw from the distribution of whether the building is cooled
    psi = NEW_IS_COOLED_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)
    
    ##################################################
    # DRAW FROM THE COP DISTRIBUTION
    # HINT: This is where you can adjust the COP values
    COP = COP_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)

    ##################################################
    # DRAW FROM THE THERMAL POWER DEMAND DISTRIBUTION
    P_TH = PTH_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY)

    ################################
    # DRAW FROM THE NH DISTRIBUTION
    # IMPORTANT: don't forget to calculate the EXPONENT of the random values for NH
    NH = np.exp(NH_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY))
     
    ##################################################
    # APPLY THE SCALING OF NH WITH THE CDD
    ##################################################
    NH = NH * SCENARIO_CDD / 213.7

    ################################
    # DRAW FROM THE AREA DISTRIBUTION
    # IMPORTANT: don't forget to calculate the EXPONENT of the random values for A
    A = np.exp(A_DISTRIBUTION.rvs(NUMBER_OFFICES_IN_SWITZERLAND_TODAY))

    ################################
    # Apply the cooling model
    E_el_cool = psi * A * NH * P_TH / COP

    ##########################################
    # Calculate the sum of the cooling demand
    # Convert the result from kWh to GWh     
    E_cooling_total = np.sum(E_el_cool) / 1000000

    results.append(E_cooling_total)
    
print('Mean: ', np.mean(results))
print('Standard Deviation: ', np.std(results))

### Run the function using the values for RCP2.6 and RCP8.5

- You can copy paste the code above into the cells below and change the numbers using the inputs from the table

## Investigate the impact of improvements to COP

Investigate how the total cooling power demand changes if the COP is improved by 50%. Simulate this by increasing the values of the COP from the distribution by 50%. 

- You can copy paste the code above for the two RCPs into the cells below and modify it adjust the COP.